# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [35 EVs per week test]

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [2]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

Cloning into 'RL_VPP_Thesis'...
remote: Enumerating objects: 503, done.
remote: Counting objects: 100% (110/110), done.
remote: Compressing objects: 100% (55/55), done.
remote: Total 503 (delta 55), reused 107 (delta 54), pack-reused 393
Receiving objects: 100% (503/503), 184.47 MiB | 22.39 MiB/s, done.
Resolving deltas: 100% (204/204), done.
Checking out files: 100% (226/226), done.
/content/RL_VPP_Thesis
Agent_trainer_notebooks/          log.log          VPP_environment.py
Algorithm_simulator_notebooks/    __pycache__/     VPP_simulator.ipynb
data/                             README.md        wandb/
EV_experiment_notebooks/          RL_VPP_Thesis/
Hyperparameters_sweep_notebooks/  trained_models/


In [3]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [4]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [5]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
#case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f8899508350>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 35
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 35, 'EVs_n_max': 1827, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [6]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [7]:
env.plot_ELVIS_data()

In [8]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  34177.29 , over-consume=kWh  49757.95 , under-consume=kWh  15580.66 , Total_cost=€  1301.74 , overcost=€  1762.89 , Av.EV_en_left=kWh  100.0 , Charging_events=  1825 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  64.34
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [9]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [10]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
#env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [23]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
#VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')
VPP_table = env.VPP_table

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  35146.56 , over-consume=kWh  50770.36 , under-consume=kWh  15623.81 , Total_cost=€  1305.77 , overcost=€  1772.27 , Av.EV_en_left=kWh  100.0 , Charging_events=  1825 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  64.34
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -619.13 , over-consume=KWh  1387.98 , under-consume=KWh  2007.11 , Total_cost=€  -4.45 , Overcost=€  50.14 
 EV_INFO: Av.EV_energy_leaving=kWh  61.21 , Std.EV_energy_leaving=kWh  23.68 , EV_departures =  1821 , EV_queue_left =  4
SCORE:  Cumulative_reward= 484365.88 - Step_rewars (load_t= 451993.3, EVs_energy_t= -5011.22)
 - Final_rewards (EVs_energy= 21270.17, Overconsume= -299.52, Underconsume= 1788.38, Overcost= 14624.78)
Episode:1 Score:484365.88466827985


In [24]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [25]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  78.058365  23.379120  57.065144  48.703178   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  85.388992  58.789482  56.028770  62.788383   
2022-06-06 05:00:00  86.105186  59.505676  56.744965  63.504578   
2022-06-06 05:15:00  86.894409  60.294899  57.534187  64.293800   
2022-06-06 05:30:00  87.663895  61.064388  58.303677  65.063286   
2022-06-06 05:45:00  88.375694  61.776188  59.015476  65.775085   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [0, 2, 1, 1]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 2, 1, 2]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 2, 2]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 2, 2]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 1, 2, 0]   
...                                           ...           ...   
2022-06-06 04:45:00  [20863, 20861, 20862, 20864]  [1, 1, 1, 1]   
2022-06-06 05:00:00  [20863, 20861, 20862, 20864]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [20863, 20861, 20862, 20864]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [20863, 20861, 20862, 20864]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [20863, 20861, 20862, 20864]  [1, 1, 1, 1]   

                                       mask_truth  ev_charged_pwr  \
time                                                                
2022-01-01 00:00:00   [True, False, False, False]        0.000000   
2022-01-01 00:15:00  [False, False, False, False]        2.000000   
2022-01-01 00:30:00  [False, False, False, False]        0.000000   
2022-01-01 00:45:00  [False, False, False, False]        0.000000   
2022-01-01 01:00:00   [False, False, False, True]        0.000000   
...                                           ...             ...   
2022-06-06 04:45:00      [True, True, True, True]       10.286002   
2022-06-06 05:00:00      [True, True, True, True]       11.459119   
2022-06-06 05:15:00      [True, True, True, True]       12.627569   
2022-06-06 05:30:00      [True, True, True, True]       12.311821   
2022-06-06 05:45:00      [True, True, True, True]       11.388797   

                     ev_discharged_pwr      load  load_reward   EV_reward  \
time                                                                        
2022-01-01 00:00:00           0.000000  1.904482    15.000000 -142.612793   
2022-01-01 00:15:00          -5.203776  0.000000    -4.436564    0.000000   
2022-01-01 00:30:00           0.000000  3.161938    -2.160996    0.000000   
2022-01-01 00:45:00           0.000000  1.796598    -2.226294    0.000000   
2022-01-01 01:00:00           0.000000  1.835777    -1.204297    0.000000   
...                                ...       ...          ...         ...   
2022-06-06 04:45:00          -1.000000  0.000000    15.000000    0.000000   
2022-06-06 05:00:00           0.000000  0.000000    15.000000    0.000000   
2022-06-06 05:15:00           0.000000  0.000000    15.000000    0.000000   
2022-06-06 05:30:00           0.000000  0.000000    15.000000    0.000000   
2022-06-06 05:45:00           0.000000  0.000000    15.000000    0.000000   

                        rewards  
time                             
2022-01-01 00:00:00 -127.612793  
2022-01-01 00:15:00   -4.436564  
2022-01-01 00:30:00   -2.160996  
2022-01-01 00:45:00   -2.226294  
2022-01-01 01:00:00   -1.204297  
...                         ...  
2022-06-06 04:45:00   15.000000  
2022-06-06 05:00:00   15.000000  
2022-06-06 05:15:00   15.000000  
2022-06-06 

In [26]:
#env.plot_Elvis_results()

In [27]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [28]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [29]:
env.plot_VPP_Elvis_comparison()

In [30]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [31]:
env.plot_rewards_stats()

In [32]:
env.plot_EVs_kpi()

In [33]:
env.plot_load_kpi()

In [34]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [35]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 21901, Arrival time: 2022-01-01 12:30:00, Parking_time: 24, Leaving_time: 2022-01-02 12:30:00, SOC: 0.45002365133714267, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 23725, Arrival time: 2022-12-31 23:15:00, Parking_time: 24, Leaving_time: 2023-01-01 23:15:00, SOC: 0.521745015783876, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  24784.41 , over-consume=kWh  44252.27 , under-consume=kWh  19467.86 , Total_cost=€  1143.93 , overcost=€  1955.04 , Charging_events=  1825 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  67.66


In [36]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [37]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [38]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  26349.91 , over-consume=kWh  45748.03 , under-consume=kWh  19398.12 , Total_cost=€  1185.15 , overcost=€  1977.16 , Av.EV_en_left=kWh  100.0 , Charging_events=  1825 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  67.66
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -2294.55 , over-consume=KWh  827.97 , under-consume=KWh  3122.52 , Total_cost=€  -78.81 , Overcost=€  35.99 
 EV_INFO: Av.EV_energy_leaving=kWh  65.04 , Std.EV_energy_leaving=kWh  23.1 , EV_departures =  1820 , EV_queue_left =  1
SCORE:  Cumulative_reward= 509914.92 - Step_rewars (load_t= 446488.22, EVs_energy_t= 19927.33)
 - Final_rewards (EVs_energy= 24081.11, Overconsume= 1901.49, Underconsume= 975.74, Overcost= 16541.03)
Episode:1 Score:509914.92298050807


In [39]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [40]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  70.599533  31.839678  63.322357  78.866234   
2022-06-06 05:00:00  71.848236  31.589678  64.571060  80.114937   
2022-06-06 05:15:00  72.735107  32.476551  65.457932  81.001808   
2022-06-06 05:30:00  73.613434  33.354877  66.336258  81.880135   
2022-06-06 05:45:00  74.443909  34.185349  67.166733  82.710609   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 04:45:00  [26330, 26331, 26329, 26332]  [1, 2, 1, 1]   
2022-06-06 05:00:00  [26330, 26331, 26329, 26332]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [26330, 26331, 26329, 26332]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [26330, 26331, 26329, 26332]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [26330, 26331, 26329, 26332]  [1, 1, 1, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 04:45:00    [True, False, True, True]       10.720294   
2022-06-06 05:00:00     [True, True, True, True]       14.984416   
2022-06-06 05:15:00     [True, True, True, True]       14.189962   
2022-06-06 05:30:00     [True, True, True, True]       14.053219   
2022-06-06 05:45:00     [True, True, True, True]       13.287555   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.216439    -4.761467        0.0   
2022-01-01 00:15:00                0.0 -3.856880    -5.565255        0.0   
2022-01-01 00:30:00                0.0 -4.621781    -2.816354        0.0   
2022-01-01 00:45:00                0.0 -2.689812    -4.465153        0.0   
2022-01-01 01:00:00                0.0 -3.679092    -4.249946        0.0   
...                                ...       ...          ...        ...   
2022-06-06 04:45:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:00:00               -1.0  0.000000    15.000000        0.0   
2022-06-06 05:15:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:30:00                0.0  0.000000    15.000000        0.0   
2022-06-06 05:45:00                0.0  0.000000    15.000000        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -4.761467  
2022-01-01 00:15:00  -5.565255  
2022-01-01 00:30:00  -2.816354  
2022-01-01 00:45:00  -4.465153  
2022-01-01 01:00:00  -4.249946  
...                        ...  
2022-06-06 04:45:00  15.000000  
2022-06-06 05:00:00  15.000000  
2022-06-06 05:15:00  15.000000  
2022-06-06 05:30:00  15.000000  
2022-06-06 05:4

In [41]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [43]:
env.plot_VPP_Elvis_comparison()

In [44]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [45]:
env.plot_rewards_stats()

In [46]:
env.plot_EVs_kpi()

In [47]:
env.plot_load_kpi()

In [48]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [49]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 27376, Arrival time: 2022-01-01 08:00:00, Parking_time: 23.575431108418666, Leaving_time: 2022-01-02 07:34:31.551990, SOC: 0.563204537544106, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 29200, Arrival time: 2022-12-31 17:45:00, Parking_time: 24, Leaving_time: 2023-01-01 17:45:00, SOC: 0.4879796922242251, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21124.15 , over-consume=kWh  42478.99 , under-consume=kWh  21354.84 , Total_cost=€  972.41 , overcost=€  1764.73 , Charging_events=  1825 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  69.55


In [50]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [51]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [52]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22820.94 , over-consume=kWh  43035.91 , under-consume=kWh  20214.97 , Total_cost=€  1027.99 , overcost=€  1773.36 , Av.EV_en_left=kWh  100.0 , Charging_events=  1825 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  69.55
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -2854.0 , over-consume=KWh  519.31 , under-consume=KWh  3373.32 , Total_cost=€  -101.08 , Overcost=€  20.43 
 EV_INFO: Av.EV_energy_leaving=kWh  67.03 , Std.EV_energy_leaving=kWh  22.84 , EV_departures =  1821 , EV_queue_left =  0
SCORE:  Cumulative_reward= 531322.98 - Step_rewars (load_t= 446336.59, EVs_energy_t= 33564.38)
 - Final_rewards (EVs_energy= 24849.16, Overconsume= 7933.05, Underconsume= 828.19, Overcost= 17811.61)
Episode:1 Score:531322.977393164


In [53]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [54]:
VPP_table.head(14995)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  78.739075  42.327209  73.279083  97.462944   
2022-06-06 03:45:00  79.420784  42.077209  73.029083  98.144653   
2022-06-06 04:00:00  80.398712  41.827209  72.779083  99.122581   
2022-06-06 04:15:00  81.466370  41.577209  72.529083  99.989998   
2022-06-06 04:30:00  82.548409  41.327209  72.279083  99.989998   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 03:30:00  [31798, 31797, 31796, 31795]  [1, 2, 2, 1]   
2022-06-06 03:45:00  [31798, 31797, 31796, 31795]  [1, 2, 2, 1]   
2022-06-06 04:00:00  [31798, 31797, 31796, 31795]  [1, 2, 2, 1]   
2022-06-06 04:15:00  [31798, 31797, 31796, 31795]  [1, 2, 2, 1]   
2022-06-06 04:30:00  [31798, 31797, 31796, 31795]  [1, 2, 2, 1]   

                                      mask_truth  ev_charged_pwr  \
time                                                               
2022-01-01 00:00:00  [False, False, False, True]        0.000000   
2022-01-01 00:15:00  [False, False, False, True]        0.000000   
2022-01-01 00:30:00  [False, False, False, True]        0.000000   
2022-01-01 00:45:00  [False, False, False, True]        0.000000   
2022-01-01 01:00:00   [False, True, False, True]        0.000000   
...                                          ...             ...   
2022-06-06 03:30:00  [True, False, False, False]        5.117245   
2022-06-06 03:45:00  [True, False, False, False]        5.453685   
2022-06-06 04:00:00  [True, False, False, False]        7.823452   
2022-06-06 04:15:00  [True, False, False, False]        7.740301   
2022-06-06 04:30:00  [True, False, False, False]        4.328154   

                     ev_discharged_pwr      load  load_reward  EV_reward  \
time                                                                       
2022-01-01 00:00:00                0.0 -3.187228    -4.503414        0.0   
2022-01-01 00:15:00                0.0 -3.702048    -3.812757        0.0   
2022-01-01 00:30:00                0.0 -3.287654    -3.583305        0.0   
2022-01-01 00:45:00                0.0 -3.149983    -6.499990        0.0   
2022-01-01 01:00:00                0.0 -5.649989    -5.725507        0.0   
...                                ...       ...          ...        ...   
2022-06-06 03:30:00               -2.0  0.000000    15.000000        0.0   
2022-06-06 03:45:00               -2.0  0.000000    15.000000        0.0   
2022-06-06 04:00:00               -2.0  0.000000     2.985705        0.0   
2022-06-06 04:15:00               -2.0 -0.800953    -5.298307        0.0   
2022-06-06 04:30:00               -2.0 -4.328137    -5.163796        0.0   

                       rewards  
time                            
2022-01-01 00:00:00  -4.503414  
2022-01-01 00:15:00  -3.812757  
2022-01-01 00:30:00  -3.583305  
2022-01-01 00:45:00  -6.499990  
2022-01-01 01:00:00  -5.725507  
...                        ...  
2022-06-06 03:30:00  15.000000  
2022-06-06 03:45:00  15.000000  
2022-06-06 04:00:00   2.985705  
2022-06-06 04:15:00  -5.298307  
2022-06-06 04:3

In [55]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [56]:
env.plot_VPP_supply_demand()

Output hidden; open in https://colab.research.google.com to view.

In [57]:
env.plot_VPP_Elvis_comparison()

In [58]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [59]:
env.plot_rewards_stats()

In [60]:
env.plot_EVs_kpi()

In [61]:
env.plot_actions_kpi()

In [62]:
env.plot_load_kpi()

In [63]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [64]:
#env.close()